In [ ]:
#using Pkg;
#Pkg.add(url="https://github.com/FerreolS/OptimPackNextGen.jl",rev="verbose")

In [1]:
include("../src/SphereIFSCalib.jl")

using TwoDimensional, Zygote, StatsBase, Plots, OptimPackNextGen, FITSIO, DelimitedFiles, Tables, DataFrames, Statistics
#using HypothesisTests #contient ChisqTest
using CSV

In [2]:
plotly()

┌ Warning: Kaleido is not available on this system. Julia will be unable to save images of any plots.
└ @ PlotlyBase /home/user/.julia/packages/PlotlyBase/GDbp9/src/kaleido.jl:65
┌ Warning: ErrorException("Could not start Kaleido process")
└ @ PlotlyBase /home/user/.julia/packages/PlotlyBase/GDbp9/src/kaleido.jl:66


Plots.PlotlyBackend()

### Constantes

In [3]:
# wavelengths
const λ1 = 987.72e-9# laser 1 
const λ2 = 1123.71e-9# laser 2 
const λ3 = 1309.37e-9# laser 3
#const λ4 = 1545.10e-9  # laser 4  
λlaser = [λ1,λ2,λ3]
λ0 = mean(λlaser);# reference
wavelengthrange = LinRange(850e-9,1600e-9,50); # coarse wavelength range of the instrument

## Fit global sur l'ensemble des lenslets:

On definit les parametres qui servent a creer le modele:
a l'amplitude maximale des spots gaussien,
fwhm la largeur a mi hauteur des spots,
cx les coefficients polynomiaux le long de l'axe x,
cy les coefficients polynomiaux le long de l'axe y

### Exemple

In [ ]:
#Bbox of the lenslet: box autour d'un set de 3 gaussiennes
bbox = BoundingBox(xmin=1012, ymin=1048, xmax=1018, ymax=1092);
a0 = [300.0 , 400.0, 500.0];
fwhm0 = [2.0, 2.0 , 2.0];
#affichage d'un exemple de trois gaussiennes avec la bbox sur les donnees reelles:
exemple = FITS("/home/user/stage/HR_4796-HD_95086/IFS_calib_wave_corrected.fits")
data= read(exemple[1]);
exempleData = data[1013:1017 , 1050:1090]
heatmap(exempleData, title = "Lenslet correspondant a la bbox initiale (exemple)", aspect_ratio = 1)

On peut deduire de cette image la taille de la bounding box d'une lenslet: hauteur 4 pixels, largeur 40 pixels.
Il manque les coeff C0 pour pouvoir fiter les gaussiennes, qu'on recupere dans des fichiers txt

### 1 lecture des fichiers txt

On veut recuperer en sortie de fonction la premiere colonne (c0, coef a l'ordre 0, soit le centre de la lenslet).

x(λ) = cx0 + cx1*((λ-λ0)/λ0) + cx2*((λ-λ0)/λ0)²

y(λ) = cy0 + cy1*((λ-λ0)/λ0) + cy2*((λ-λ0)/λ0)²

On donne ici λ en metre, dans le code Matlab λ est en micronmetre. Il faut donc normaliser et convertir les coefficients c1 et c2. 

In [4]:
coeffx = readdlm("/home/user/stage/HR_4796-HD_95086/Calibration_wave_spec/coef_pol_x.txt", header = false)
cx0 = coeffx[:,1];
cx1 = coeffx[:,2]*λ0*1e6;
cx2 = coeffx[:,3]*λ0^2*1e12;

coeffy = readdlm("/home/user/stage/HR_4796-HD_95086/Calibration_wave_spec/coef_pol_y.txt", header = false)
cy0 = coeffy[:,1];
cy1 = coeffy[:,2]*λ0*1e6;
cy2 = coeffy[:,3]*λ0^2*1e12;

### Histogrammes

In [117]:
histogram([cx1 cx2], title = "cx Anthony", bins = LinRange(-5,9,100), 
    label = ["cx1" "cx2"], xlabel = "position", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [118]:
histogram([cy1 cy2], title = "cy Anthony", bins = LinRange(-100,130,100), 
    label = ["cy1" "cy2"], xlabel = "position", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [120]:
histogram(cy1, title = "cy1 Anthony", bins = LinRange(100,105,100), 
    label = "cy1", xlabel = "position", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [121]:
cy2_anthony = histogram(cy2, title = "cy2 Anthony", bins = LinRange(-100,-25,100), 
    label = "cy2", xlabel = "position", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

### 2 ouvrir et trouver positions dans l'image brute

1/ IFS_sim_wave.fits: on ouvre le modele, qui a peu de BP, donc les fit des lenslets seront bons. f5 = FITS("/home/user/Pictures/IFS_sim_wave.fits")

2/ IFS_calib_wave_corrected: "vrai" fichier de depart (a comparer avec 1/ eventuellement)

In [9]:
laserData = FITS("/home/user/stage/HR_4796-HD_95086/IFS_calib_wave_corrected.fits", "r");

In [10]:
#Read the data or a subset thereof from disk, and save it in a pre-allocated output array A.
A =zeros(2048,2048); #pre-allocate matrix A
read!(laserData[1], A); #data

In [11]:
close(laserData);

In [123]:
#Constantes
ainit = [1. , 1. , 1.];
fwhminit = [3.0, 3.0 , 3.0];
laser =  LaserModel(λlaser,ainit,fwhminit);
Cinit = zeros(2,laser.nλ);

#BoundingBox
largeur = 4;
hauteur = 40;
dxmin = round(Int, largeur/2);
dxmax = round(Int, largeur/2);
dymin = round(Int, hauteur/2);
dymax = round(Int, hauteur/2);
mcx1 = median(cx1);
mcy1 = median(cy1);
mcx2 = median(cx2);
mcy2 = median(cy2);

N = length(cx0) #Nombre de lenslet (18908)

valid = (round.(cx0 .- dxmin).>0) .&  (round.(cx0 .+ dxmax).<2048) .&  
(round.(cy0 .- dymin).>0) .&  (round.(cy0 .+ dymax).<2048);

In [124]:
#Initialiser tableaux de resultats avec possibilite d'avoir valeurs "missing"
atab = Array{Union{Float64,Missing}}(missing,3,N); #zeros(3,N);
fwhmtab = Array{Union{Float64,Missing}}(missing,3,N); #zeros(3,N);
ctab = Array{Union{Float64,Missing}}(missing,2,3,N); #zeros(2,3,N);
lmodtab = Array{Union{LensletModel,Missing}}(missing,N); #Array{LensletModel}(undef,N);

xmin = cx0[i,1]-largeur/2 lenslet, ymin = cy0[i,1]-hauteur/2 lenslet

xmax = cx0[i,1]+largeur/2 lenslet, ymax = cy0[i,1]+hauteur/2 lenslet

Remarque: centre de l'image 0 = 1025x1025 pixel, donc il faut ajouter 1025 a xmin et xmax, ymin et ymax 

### Ensemble des lenslet

In [125]:
@time Threads.@threads for i in collect(1:N)[valid] #indice des lenslet valides
    #Initialisation
    cx0i = cx0[i,1] .+1025; #centre de la lenslet
    cy0i = cy0[i,1] .+1025;

    xmin=cx0i-dxmin;
    xmax=cx0i+dxmax;
    ymin=cy0i-dymin;
    ymax=cy0i+dymax; 
    if ymax>2048
        continue
    end 
    bbox = round(Int, BoundingBox(xmin, xmax, ymin, ymax));
    
    lmodtab[i] = LensletModel(λ0,laser.nλ-1, bbox); #contient le model pour chaque lenslet
    
    Cinit = [ [cx0i mcx1 mcx2]; [cy0i mcy1 mcy2] ]; #[1:2,1:3]
    
    #Fit du polynome pour chaque lenslet: optimisation
    ldata = view(A, bbox);    #lenslet laser data
    lkl = LikelihoodIFS(lmodtab[i], deepcopy(laser), ldata);
    cost(x::Vector{Float64}) = lkl(x);
    xinit = vcat([ainit[:],fwhminit[:],Cinit[:]]...);
    
    try #The try/catch statement allows for Exceptions to be tested for. much slower than using conditional branching
        xopt = vmlmb(cost, xinit; verb=false, maxeval=500);
        #Sauvegarde des valeurs des parametres du modele dans des vecteurs
        #ce qu'on veut garder: lmod sous forme de vecteur, 1 modele de lenslet par lenslet
        (aopt,fwhmopt,copt) = (xopt[1:(laser.nλ)],xopt[(laser.nλ+1):(2*laser.nλ)],reshape(xopt[(2*laser.nλ+1):(4*laser.nλ)],2,:));
        atab[:,i] = aopt
        fwhmtab[:,i] = fwhmopt
        ctab[:,:,i]  = copt
    catch       #the symbol following catch will always be interpreted as a name for the exception
        continue
    end
        
    print(i)
end


2891011202122232526383940414345466263656769717273929395979910110310410510612812913113313513713914114214314417017117317517717918118318518618718818921922122322522722923123323523623723823924027327527727928128328528728929129229329429529633333533733934134334534734935135335435535635735835939940140340540740941141341541741942142242342442542642742847147347547747948148348548748949149349549649749849950050150255155355555755956156356556756957157357557657757857958058158258363563763964164364564764965165365565765966166266366466566666766866967072572772973173373573773974174374574774975175375475575675775875976076176282182382582782983183383583783984184384584784985185285385485585685785885986086192392592792993193393593793994194394594794995195395595695795895996096196296396496596610331035103710391041104310451047104910511053105510571059106110631065106610671068106910701071107210731074107510761147114911511153115511571159116111631165116711691171117311751177117911811182118311841185118611871188118911901191119211931

8389839083918392839383948395839683978398839984008401840284038404840584068407840884098607860986118613861586178619862186238625862786298631863386358637863986418643864586478649865186538655865786598661866386658667866986718673867586778679868186838685868786898691869386958696869786988699870087018702870387048705870687078708870987108711871287138714871587168717871887198720872187228723872487258726872787288729873089318933893589378939894189438945894789498951895389558957895989618963896589678969897189738975897789798981898389858987898989918993899589978999900190039005900790099011901390159017901990219022902390249025902690279028902990309031903290339034903590369037903890399040904190429043904490459046904790489049905090519052905390549055905692619263926592679269927192739275927792799281928392859287928992919293929592979299930193039305930793099311931393159317931993219323932593279329933193339335933793399341934393459347934993519353935493559356935793589359936093619362936393649365936693679368936993709371937293739374

1522415226152281523015232152341523615238152401524215244152461524815250152521525415256152581526015262152641526615268152701527115272152731527415275152761527715278152791528015281152821528315284152851528615287152881528915290152911529215293152941529515296152971529815299153001530115302153031530415305153061530715506155081551015512155141551615518155201552215524155261552815530155321553415536155381554015542155441554615548155501555215554155561555815560155621556415566155681557015572155741557615578155801558215584155861558815590155921559415596155981560015602156041560615608156101561215614156161580515807158091581115813158151581715819158211582315825158271582915831158331583515837158391584115843158451584715849158511585315855158571585915861158631586515867158691587115873158751587715879158811588315885158871588915891158931589515897158991590115903159051590715909160931609516097160991610116103161051610716109161111611316115161171611916121161231612516127161291613116133161351613716139161411614316145161471614916151

In [126]:
#Sans carte BP
atab_valid = collect(skipmissing(atab));
fwhmtab_valid = collect(skipmissing(fwhmtab));
ctab_valid = collect(skipmissing(ctab));
#separation de ctab en cxtab et cytab
cxtab = reshape(ctab_valid[:,1,1],2,: )[1,:,:];
reshape(cxtab,3,:);
cytab = reshape(ctab_valid[:,1,1],2,: )[2,:,:];
reshape(cytab,3,:);

In [127]:
CSV.write("atab.csv",  DataFrame(reshape(atab_valid, 3 , : ), :auto));
CSV.write("fwhmtab.csv",  DataFrame(reshape(fwhmtab_valid, 3, :), :auto));
CSV.write("cxtab.csv",  DataFrame(reshape(cxtab,3,:), :auto));
CSV.write("cytab.csv",  DataFrame(reshape(cytab,3,:), :auto));

## Avec BP

In [14]:
badpix = Float64.(read(FITS("/home/user/stage/HR_4796-HD_95086/IFS_BP_corrected.fits")[1]));

In [128]:
@time Threads.@threads for i in collect(1:N)[valid] #indice des lenslet valides
    #Initialisation
    cx0i = cx0[i,1] .+1025; #centre de la lenslet
    cy0i = cy0[i,1] .+1025;

    xmin=cx0i-dxmin;
    xmax=cx0i+dxmax;
    ymin=cy0i-dymin;
    ymax=cy0i+dymax; 
    if ymax>2048
        continue
    end 
    bbox = round(Int, BoundingBox(xmin, xmax, ymin, ymax));
    
    lmodtab[i] = LensletModel(λ0,laser.nλ-1, bbox); #contient le model pour chaque lenslet
    
    Cinit = [ [cx0i mcx1 mcx2]; [cy0i mcy1 mcy2] ]; #[1:2,1:3]
    
    #Fit du polynome pour chaque lenslet: optimisation
    ldata = view(A, bbox);    #lenslet laser data
    badpixview = view(badpix,bbox)
    lkl = LikelihoodIFS(lmodtab[i], deepcopy(laser), ldata, badpixview);
    cost(x::Vector{Float64}) = lkl(x);
    xinit = vcat([ainit[:],fwhminit[:],Cinit[:]]...);
    
    try #The try/catch statement allows for Exceptions to be tested for. much slower than using conditional branching
        xopt = vmlmb(cost, xinit; verb=false, maxeval=500);

        #Sauvegarde des valeurs des parametres du modele dans des vecteurs
        #ce qu'on veut garder: lmod sous forme de vecteur, 1 modele de lenslet par lenslet
        (aopt,fwhmopt,copt) = (xopt[1:(laser.nλ)],xopt[(laser.nλ+1):(2*laser.nλ)],reshape(xopt[(2*laser.nλ+1):(4*laser.nλ)],2,:));
        atab[:,i] = aopt
        fwhmtab[:,i] = fwhmopt
        ctab[:,:,i]  = copt
    catch       #the symbol following catch will always be interpreted as a name for the exception
        continue
    end
        
    print(i)
end


2891011202122232526383940414345466263656769717273929395979910110310410510612812913113313513713914114214314417017117317517717918118318518618718818921922122322522722923123323523623723823924027327527727928128328528728929129229329429529633333533733934134334534734935135335435535635735835939940140340540740941141341541741942142242342442542642742847147347547747948148348548748949149349549649749849950050150255155355555755956156356556756957157357557657757857958058158258363563763964164364564764965165365565765966166266366466566666766866967072572772973173373573773974174374574774975175375475575675775875976076176282182382582782983183383583783984184384584784985185285385485585685785885986086192392592792993193393593793994194394594794995195395595695795895996096196296396496596610331035103710391041104310451047104910511053105510571059106110631065106610671068106910701071107210731074107510761147114911511153115511571159116111631165116711691171117311751177117911811182118311841185118611871188118911901191119211931

8389839083918392839383948395839683978398839984008401840284038404840584068407840884098607860986118613861586178619862186238625862786298631863386358637863986418643864586478649865186538655865786598661866386658667866986718673867586778679868186838685868786898691869386958696869786988699870087018702870387048705870687078708870987108711871287138714871587168717871887198720872187228723872487258726872787288729873089318933893589378939894189438945894789498951895389558957895989618963896589678969897189738975897789798981898389858987898989918993899589978999900190039005900790099011901390159017901990219022902390249025902690279028902990309031903290339034903590369037903890399040904190429043904490459046904790489049905090519052905390549055905692619263926592679269927192739275927792799281928392859287928992919293929592979299930193039305930793099311931393159317931993219323932593279329933193339335933793399341934393459347934993519353935493559356935793589359936093619362936393649365936693679368936993709371937293739374

1522415226152281523015232152341523615238152401524215244152461524815250152521525415256152581526015262152641526615268152701527115272152731527415275152761527715278152791528015281152821528315284152851528615287152881528915290152911529215293152941529515296152971529815299153001530115302153031530415305153061530715506155081551015512155141551615518155201552215524155261552815530155321553415536155381554015542155441554615548155501555215554155561555815560155621556415566155681557015572155741557615578155801558215584155861558815590155921559415596155981560015602156041560615608156101561215614156161580515807158091581115813158151581715819158211582315825158271582915831158331583515837158391584115843158451584715849158511585315855158571585915861158631586515867158691587115873158751587715879158811588315885158871588915891158931589515897158991590115903159051590715909160931609516097160991610116103161051610716109161111611316115161171611916121161231612516127161291613116133161351613716139161411614316145161471614916151

In [129]:
#Avec carte BP
atabBP_valid = collect(skipmissing(atab));
fwhmtabBP_valid = collect(skipmissing(fwhmtab));
ctabBP_valid = collect(skipmissing(ctab));
#separation de ctab en cxtab et cytab
cxtabBP = reshape(ctabBP_valid[:,1,1],2,: )[1,:,:];
reshape(cxtabBP,3,:);
cytabBP = reshape(ctabBP_valid[:,1,1],2,: )[2,:,:];
reshape(cytabBP,3,:);

In [130]:
CSV.write("atabBP.csv",  DataFrame(reshape(atabBP_valid, 3 , : ), :auto));
CSV.write("fwhmtabBP.csv",  DataFrame(reshape(fwhmtabBP_valid, 3, :), :auto));
CSV.write("cxtabBP.csv",  DataFrame(reshape(cxtabBP,3,:), :auto));
CSV.write("cytabBP.csv",  DataFrame(reshape(cytabBP,3,:), :auto));

## Affichage

### Statistique

#### sans BP

In [138]:
a_csv = CSV.read("atab.csv", DataFrame; datarow = 1, transpose = true);
a0_hist = (a_csv[:,2]); #2eme colonne
a1_hist = (a_csv[:,3]);
a2_hist = (a_csv[:,4]);
histogram([a0_hist a1_hist a2_hist], title = "amplitudes sans BP", label = ["a0" "a1" "a2"],
    bins = LinRange(-200,1500,100), xlabel = "position", ylabel = "amplitude")

<!DOCTYPE html>
 
 
 Plots.jl

In [142]:
fwhm_csv = CSV.read("fwhmtab.csv", DataFrame; datarow = 1, transpose=true);
fwhm0_hist = (fwhm_csv[:,2]);
fwhm1_hist = (fwhm_csv[:,3]);
fwhm2_hist = (fwhm_csv[:,4]);
histogram([fwhm0_hist fwhm1_hist fwhm2_hist], title = "fwhm sans BP", label = ["fwhm0" "fwhm1" "fwhm2"],
    bins = LinRange(1.5,3.5, 100),  xlabel = "position", ylabel = "fwhm", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [145]:
cx_csv = CSV.read("cxtab.csv", DataFrame; datarow = 1, transpose=true);
cx1_hist = (cx_csv[:,3]);
cx2_hist = (cx_csv[:,4]);
histogram([cx1_hist cx2_hist], title = "cx sans BP", label = ["cx1" "cx2"],
    bins = LinRange(-20,20,100), xlabel = "position", ylabel = "cx", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [149]:
cy_csv = CSV.read("cytab.csv", DataFrame; datarow = 1, transpose=true);
cy1_hist = (cy_csv[:,3]);
cy2_hist = (cy_csv[:,4]);
histogram([cy1_hist cy2_hist], title = "cy sans BP", label = ["cy1" "cy2"],
     bins = LinRange(-100,200,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [160]:
histogram(cy1_hist, title = "cy1 sans BP", label = "cy1",
     bins = LinRange(95,110,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [157]:
histogram(cy2_hist, title = "cy2 sans BP", label = "cy2",
     bins = LinRange(-150,100,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

#### avec BP

In [164]:
aBP_csv = CSV.read("atabBP.csv", DataFrame; datarow = 1, transpose = true);
a0BP_hist = (aBP_csv[:,2]);
a1BP_hist = (aBP_csv[:,3]);
a2BP_hist = (aBP_csv[:,4]);
histogram([a0BP_hist a1BP_hist a2BP_hist], title = "amplitudes avec BP", label = ["a0" "a1" "a2"],
    bins = LinRange(-200,1500, 100), xlabel = "position", ylabel = "amplitude")

<!DOCTYPE html>
 
 
 Plots.jl

In [166]:
fwhmBP_csv = CSV.read("fwhmtabBP.csv", DataFrame; datarow = 1, transpose=true);
fwhm0BP_hist = (fwhmBP_csv[:,2]);
fwhm1BP_hist = (fwhmBP_csv[:,3]);
fwhm2BP_hist = (fwhmBP_csv[:,4]);
histogram([fwhm0BP_hist fwhm1BP_hist fwhm2BP_hist], title = "fwhm avec BP", label = ["fwhm0" "fwhm1" "fwhm2"],
    bins = LinRange(1.5,3.5,100), xlabel = "position", ylabel = "fwhm")

<!DOCTYPE html>
 
 
 Plots.jl

In [168]:
cxBP_csv = CSV.read("cxtabBP.csv", DataFrame; datarow = 1, transpose=true);
cx1BP_hist = (cxBP_csv[:,3]);
cx2BP_hist = (cxBP_csv[:,4]);
histogram([cx1BP_hist cx2BP_hist], title = "cx avec BP", label = ["cx1" "cx2"],
    bins = LinRange(-20,20,100), xlabel = "position", ylabel = "cx", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [170]:
cyBP_csv = CSV.read("cytabBP.csv", DataFrame; datarow = 1, transpose=true);
cy1BP_hist = (cyBP_csv[:,3]);
cy2BP_hist = (cyBP_csv[:,4]);
histogram([cy1BP_hist cy2BP_hist], title = "cy avec BP", label = ["cy1" "cy2"],
     bins = LinRange(-100,200,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [172]:
histogram(cy1BP_hist, title = "cy1 avec BP", label = "cy1",
     bins = LinRange(96,110,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

In [174]:
histogram(cy2BP_hist, title = "cy2 avec BP", label = "cy2",
     bins = LinRange(-150,100,100), xlabel = "position", ylabel = "cy", legend = :best)

<!DOCTYPE html>
 
 
 Plots.jl

### Lenslet

In [ ]:
x_axis = range(bbox.xmin, bbox.xmax, length = bbox.xmax-bbox.xmin+1);
y_axis = range(bbox.ymin, bbox.ymax, length = bbox.ymax-bbox.ymin+1);

In [ ]:
plt = scatter([cx0i], [cy0i], color=["gold"], label = "centre Anthony");
heatmap!(plt,x_axis, y_axis,  transpose(ldata), clim = (-80,80),
    xlabel = "x", ylabel = "y", xrange = [xmin-10, xmax+10], aspect_ratio = 1, legend = :bottomright)

In [ ]:
#Point de depart de l'optimiseur
UpdateDispModel(lmodtab[i].dmodel, Cinit);
UpdateLaserModel(laser,ainit,fwhminit);
limageinit = LensletLaserImage(lmodtab[i],laser)
plt = scatter([cx0i], [cy0i], color=["red"], label = "Initialisation");
heatmap!(plt, x_axis, y_axis,  transpose(limageinit), title = "Initialisation", 
    xlabel = "x", ylabel = "y", xrange = [xmin-10,xmax+10], clim = (-80,80), 
    aspect_ratio = 1, legend = :bottomright)

In [ ]:
#Point d'arrivee de l'optimiseur
UpdateDispModel(lmodtab[i].dmodel, copt);
UpdateLaserModel(laser,aopt,fwhmopt);
limageopt = LensletLaserImage(lmodtab[i],laser)
plt = scatter( [cx0i;copt[1,1]], [cy0i;copt[2,1]], color = ["red" , "blue"], lab = ["initialisation" "optimisation"]);
heatmap!(plt, x_axis, y_axis,  transpose(limageopt), title = "Point d'arrivee de l'optimiseur", 
    xlabel = "x", ylabel = "y", xrange = [xmin-20,xmax+20], clim = (-80,80), 
    aspect_ratio = 1, legend = :bottomright)

In [ ]:
#Residus
heatmap(x_axis, y_axis, transpose(ldata .- limageopt), title = "Residus sans precision", 
    clim = (-80,80), xlabel = "x", ylabel = "y", xrange = [xmin-10,xmax+10], aspect_ratio = 1)

### Test avec donnees lamp
Permet de verifier si la bbox es convenable (si spectre est complet ou decoupee ou pas sur quelques lenslet)

In [ ]:
lamp = FITS("/home/user/stage/HR_4796-HD_95086/Calibration_wave_spec/IFS_sim_spec.fits", "r")
B = zeros(2048,2048);
data = read!(lamp[1], B);

In [ ]:
i = 5

xmin=(cx0[i,1] .-dxmin) .+1026;
xmax=(cx0[i,1] .+dxmax) .+1026;
ymin=(cy0[i,1] .-dymin) .+1024;
ymax=(cy0[i,1] .+dymax) .+1024;

bbox = round(Int, BoundingBox(xmin, xmax, ymin, ymax));

x_axis = range(bbox.xmin, bbox.xmax, length = bbox.xmax-bbox.xmin+1);
y_axis = range(bbox.ymin, bbox.ymax, length = bbox.ymax-bbox.ymin+1);

plt = scatter(cx0[1:10,1], cx0[1:10,1])
ldata = view(B,bbox);
heatmap(y_axis, x_axis, ldata, title = "Exemple du spectre d'une lenslet au centre")


In [ ]:
#toute l'image
bbox = BoundingBox(1, 2048, 1, 2048);
x_axis = range(bbox.xmin, bbox.xmax, length = bbox.xmax-bbox.xmin+1);
y_axis = range(bbox.ymin, bbox.ymax, length = bbox.ymax-bbox.ymin+1);
plt = scatter(cx0[:,1], cy0[:,1])
heatmap!(plt,x_axis, y_axis,  transpose(data), title = "IFS_sim_spec.fits", clim = (-80,80))

In [ ]:
f6 = FITS("/home/user/stage/HR_4796-HD_95086/IFS_calib_spec_corrected.fits", "r"); #donnees lamp
B =zeros(2048,2048); #pre-allocate matrix A  Array{Float64}(undef,2048,2048)
read!(f6[1], B);
bbox = BoundingBox(xmin=1013, xmax=1017, ymin=1050, ymax=1088);
ldata = view(B,bbox); # ex lenslet au centre de l'image [1012:1018, 1048:1092]
p1 = heatmap(ldata, title = "Exemple du spectre d'une lenslet au centre")


f7 = FITS("/home/user/stage/HR_4796-HD_95086/IFS_calib_spec_corrected.fits", "r"); #donnees lamp
C =zeros(2048,2048); #pre-allocate matrix A  Array{Float64}(undef,2048,2048)
read!(f7[1], C);
bbox = BoundingBox(xmin=214, xmax=218, ymin=272, ymax=311);
ldata = view(C,bbox); 
p2 = heatmap(ldata, title = "Exemple 1 du spectre d'une lenslet en peripherie")


f8 = FITS("/home/user/stage/HR_4796-HD_95086/IFS_calib_spec_corrected.fits", "r"); #donnees lamp
D =zeros(2048,2048); #pre-allocate matrix A  Array{Float64}(undef,2048,2048)
read!(f7[1], D);
bbox = BoundingBox(xmin=1501, xmax=1505, ymin=1574, ymax=1613);
ldata = view(D,bbox); 
p3 = heatmap(ldata, title = "Exemple 2 du spectre d'une lenslet en peripherie")


plot(p1, p2, p3, legend = false, layout = (3, 1), aspect_ratio = 1)

On voit que le spectre n'est pas decoupe.

In [ ]:
#test
plt = scatter(cx0[1:10,1] .+200, cy0[1:10,1] .+400)
heatmap!(plt,x_axis, y_axis,  transpose(data), title = "IFS_sim_spec.fits")

Methode 1: tracer des histogrammes de tous les coeff, visualisation des outliers. Ajustement d'une gaussienne, calcul de la moyenne de la variance, ce qui est superieur a 3σ est sorti.

Methode 2: test statistique par rapport au guess si methode 1 marche pas. Histogramme des valeurs de χ2

In [ ]:
#Statistics
@show std(aopt);
@show std(fwhmopt);
@show std(copt);

In [ ]:
@show var(aopt);
@show var(fwhmopt);
@show var(copt);

In [ ]:
lmod.dmodel.(λlaser)
heatmap(clamp.(ldata,0,1500), title = "Fit laser")

In [ ]:
for i in 14957:14970
    #Initialisation
    cx0i = cx0[i,1] .+1025;
    cy0i = cy0[i,1] .+1025;

    xmin=cx0i-dxmin;
    xmax=cx0i+dxmax;
    ymin=cy0i-dymin;
    ymax=cy0i+dymax; 
    if ymax>2048
        continue
    end  
    bbox = round(Int, BoundingBox(xmin, xmax, ymin, ymax));
    
    lmodtab[i] = LensletModel(λ0,laser.nλ-1, bbox); #contient le model pour chaque lenslet
     
    Cinit = [ [cx0i mcx1 mcx2]; [cy0i mcy1 mcy2] ];
    
    #Fit du polynome pour chaque lenslet: optimisation
    ldata = view(A, bbox);    #lenslet laser data
    lkl = LikelihoodIFS(lmodtab[i], laser, ldata);#rajouter carte BP
    cost(x::Vector{Float64}) = lkl(x);
    xinit = vcat([ainit[:],fwhminit[:],Cinit[:]]...);
    try
        xopt = vmlmb(cost, xinit; verb=false, maxeval=500); #verb=50

        #Sauvegarde des valeurs des parametres du modele dans des vecteurs
        (aopt,fwhmopt,copt) = (xopt[1:(laser.nλ)],xopt[(laser.nλ+1):(2*laser.nλ)],reshape(xopt[(2*laser.nλ+1):(4*laser.nλ)],2,:));
        atab[:,i] = aopt
        fwhmtab[:,i] = fwhmopt
        ctab[:,:,i]  = copt
    catch
        continue
    end
    print(i)
end
